In [1]:
# importing libraries

from __future__ import print_function
from ipywidgets import interact, interactive, fixed, interact_manual
from IPython.core.display import display, HTML

import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import plotly.express as px

import plotly.graph_objects as go
import seaborn as sns
import ipywidgets as widgets
from millify import millify

In [2]:
pd.set_option("display.max_rows", None, "display.max_columns", None)

In [3]:
# loading data right from the source:
death_df = pd.read_csv('https://raw.githubusercontent.com/CSSEGISandData/COVID-19/master/csse_covid_19_data/csse_covid_19_time_series/time_series_covid19_deaths_global.csv')
confirmed_df = pd.read_csv('https://raw.githubusercontent.com/CSSEGISandData/COVID-19/master/csse_covid_19_data/csse_covid_19_time_series/time_series_covid19_confirmed_global.csv')
recovered_df = pd.read_csv('https://raw.githubusercontent.com/CSSEGISandData/COVID-19/master/csse_covid_19_data/csse_covid_19_time_series/time_series_covid19_recovered_global.csv')
country_df = pd.read_csv('https://raw.githubusercontent.com/CSSEGISandData/COVID-19/web-data/data/cases_country.csv')
pop_df=pd.read_csv("population of all countries of the world.csv")

In [4]:
# data cleaning

# renaming the df column names to lowercase
country_df.columns = map(str.lower, country_df.columns)
confirmed_df.columns = map(str.lower, confirmed_df.columns)
death_df.columns = map(str.lower, death_df.columns)
recovered_df.columns = map(str.lower, recovered_df.columns)

# changing province/state to state and country/region to country
confirmed_df = confirmed_df.rename(columns={'province/state': 'state', 'country/region': 'country'})

recovered_df = recovered_df.rename(columns={'province/state': 'state', 'country/region': 'country'})

death_df = death_df.rename(columns={'province/state': 'state', 'country/region': 'country'})

country_df = country_df.rename(columns={'country_region': 'country'})


# country_df.head()

In [5]:
test=confirmed_df.iloc[30:40]

In [6]:
def removeDuplict(df):

    df.drop(columns="state",inplace=True)
    for i in range(0,test.shape[0]):

        if df.iloc[i]["country"] == df.iloc[i-1]["country"]:
            df["lat"].iloc[i]=np.NaN
            df["long"].iloc[i]=np.NaN
    df=df.groupby(by="country").sum()
    df=df.reset_index()
    return df
    

In [7]:
confirmed_df=removeDuplict(confirmed_df)

C:\Users\ibrahim\Anaconda3\lib\site-packages\pandas\core\indexing.py:190: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy



In [8]:
recovered_df=removeDuplict(recovered_df)

In [9]:
confirmed_df.country.drop_duplicates(inplace=True)

In [10]:
country_df.sort_values(by="confirmed" , ascending=False,inplace=True)


In [11]:
# total number of confirmed, death and recovered cases
confirmed_total = int(country_df['confirmed'].sum())
deaths_total = int(country_df['deaths'].sum())
recovered_total = int(country_df['recovered'].sum())
active_total = int(country_df['active'].sum())

In [12]:
activeCase=confirmed_df.copy()

In [13]:
country_df=pd.merge(country_df,pop_df[["iso3","population"]],on="iso3")

In [14]:
pr=[]
for i in range(len(country_df)):
    pr.append("{0:.2%}".format(country_df["confirmed"][i]/country_df["population"][i]))

In [15]:
country_df["percent"]=pr

In [16]:
country_df=country_df.sort_values(by="percent",ascending=True).reset_index(drop=True)

In [17]:
activeCase=confirmed_df.copy()
activeCase.iloc[:,5:]=confirmed_df.iloc[:,5:]-recovered_df.iloc[:,5:]


In [18]:
confirmed_ON_day=confirmed_df.copy()
confirmed_ON_day.iloc[:,5:]=confirmed_df.iloc[:,5:confirmed_df.shape[1]]-confirmed_df.iloc[:,4:confirmed_df.shape[1]-1].values

In [19]:
recovered_ON_day=confirmed_df.copy()
recovered_ON_day.iloc[:,5:]=recovered_df.iloc[:,5:recovered_df.shape[1]]-recovered_df.iloc[:,4:recovered_df.shape[1]-1].values


In [20]:
GCC_confirmed_df=confirmed_df[confirmed_df["country"].isin(["Saudi Arabia","United Arab Emirates","Kuwait","Bahrain","Qatar","Oman"])].reset_index(drop=True)
GCC_recovered_df=recovered_df[recovered_df["country"].isin(["Saudi Arabia","United Arab Emirates","Kuwait","Bahrain","Qatar","Oman"])].reset_index(drop=True)
GCC_death_df=death_df[death_df["country"].isin(["Saudi Arabia","United Arab Emirates","Kuwait","Bahrain","Qatar","Oman"])].reset_index(drop=True)
GCC_country_df=country_df[country_df["country"].isin(["Saudi Arabia","United Arab Emirates","Kuwait","Bahrain","Qatar","Oman"])].reset_index(drop=True)

In [21]:
def statsic_cases(country):
    dic = dict(zip(country_df.country,country_df.iso3))
    
    display(HTML("<div style = 'background-color: #fff; padding: 30px '>" +
                 "<span style='color: #000000; font-size:25px;'> Confirmed : "  +millify(country_df[country_df["iso3"]==dic[country]]["confirmed"].sum(),precision=2)+"</span>" +
                 "<span style='color:#EB1D1D; font-size:25px;margin-left:20px;'> Deaths: " +"{0:.2%}".format(country_df[country_df["iso3"]==dic[country]]["deaths"].sum()/country_df[country_df["iso3"]==dic[country]]["confirmed"].sum())+ "</span>"+
                 "<span style='color: lightgreen; font-size:25px; margin-left:20px;'> Recovered: " +"{0:.2%}".format(country_df[country_df["iso3"]==dic[country]]["recovered"].sum()/country_df[country_df["iso3"]==dic[country]]["confirmed"].sum()) + "</span>"+
                  "<span style='color: #FFA500; font-size:25px; margin-left:20px;'> Active: " +"{0:.2%}".format(country_df[country_df["iso3"]==dic[country]]["active"].sum()/country_df[country_df["iso3"]==dic[country]]["confirmed"].sum()) + "</span><br><br>"+
                "<span style='color: #000000; font-size:25px;'> Population : "  + millify(pop_df[pop_df["iso3"]==dic[country]]["population"].sum(),precision=2) +"</span>"
                 "<span style='color: #000000; font-size:25px; margin-left:20px;'><br><br> The percentage of confirmed cases from the popluation : "+"{0:.2%}".format(country_df[country_df["iso3"]==dic[country]]["confirmed"].sum()/pop_df[pop_df["iso3"]==dic[country]]["population"].sum())+" /100%" + "</span><br><br>"+
              "</div>")
           )

In [22]:
def plot_cases_of_a_country_on_day(country):

    labels = ['Confirmed ON day', 'Recovered ON day']
    colors = ['blue', 'green']
    mode_size = [6, 8]
    line_size = [4, 5]
    
    df_list = [confirmed_ON_day, recovered_ON_day]
    
    fig = go.Figure();
 
    for i, df in enumerate(df_list):   
            
        x_data = np.array(list(df.iloc[:, -30:].columns))
        y_data = np.sum(np.asarray(df[df['country'] == country].iloc[:,-30:]),axis = 0)

        fig.add_trace(go.Scatter(x=x_data, y=y_data, mode='lines+markers',
        name=labels[i],
        line=dict(color=colors[i], width=line_size[i]),
        connectgaps=True,
        ));  
    fig.update_layout(
        title="COVID 19 cases of " + country,
        xaxis_title='Date',
        yaxis_title='No. of Confirmed Cases',
        margin=dict(l=20, r=20, t=40, b=20),
        paper_bgcolor="lightgrey",
        width = 800,
    
    );
    
    fig.update_xaxes(tickangle=45)
    fig.update_yaxes(type="linear")
    fig.show();
    

In [23]:
def plot_cases_of_a_country(country):

    labels = ['Acive Cases', 'Recovered Cases']
    colors = ['Red', 'Blue']
    mode_size = [6, 8]
    line_size = [4, 5]
    
    df_list = [activeCase, recovered_df]
    
    fig = go.Figure();
 
    for i, df in enumerate(df_list):   
        if i == 0:   
        
            x_data = np.array(list(df.iloc[:, -45:].columns))
            y_data = np.sum(np.asarray(df[df['country'] == country].iloc[:,-45:]),axis = 0)

            fig.add_trace(go.Scatter(x=x_data, y=y_data, mode='lines+markers',
            name=labels[i],
            line=dict(color=colors[i], width=line_size[i]),
            connectgaps=True,
            text = "Total " + str(labels[i]) +": "+ str(y_data[-1])
            ));  
            
        else:
            x_data = np.array(list(df.iloc[:, -45:].columns))
            y_data = np.sum(np.asarray(df[df['country'] == country].iloc[:,-45:]),axis = 0)

            fig.add_trace(go.Scatter(x=x_data, y=y_data, mode='lines+markers',
            name=labels[i],
            line=dict(color=colors[i], width=line_size[i]),
            connectgaps=True,
            text = "Total of " + str(labels[i]) +": "+ str(y_data[-1])
            )); 
    fig.update_xaxes(tickangle=45)
    fig.update_layout(
        title="COVID 19 cases of " + country,
        xaxis_title='Date',
        yaxis_title='No. of Cases',
        margin=dict(l=20, r=20, t=40, b=20),
        paper_bgcolor="lightgrey",
        width = 800);
    
    fig.update_yaxes(type="linear")
    fig.show();
    statsic_cases(country)
    
  

In [24]:

opts=activeCase.country.values

widg=widgets.Dropdown(
    options=opts,
    value=opts[1],
    description="Country:")

#widgets.interact(plot_cases_of_a_country_on_day,country=widg)
widgets.interact(plot_cases_of_a_country,country=widg)    

interactive(children=(Dropdown(description='Country:', index=1, options=('Afghanistan', 'Albania', 'Algeria', …

<function __main__.plot_cases_of_a_country(country)>

In [25]:
test=activeCase.copy()

In [26]:
test=test.melt(id_vars=['country','lat','long'], value_vars=test.iloc[:,3:],value_name="Count",var_name="Date")

In [27]:
test.Count=test.Count.astype("int")

In [28]:
import datetime

In [29]:
test["Date"]=pd.to_datetime(test['Date'],format='%m/%d/%y')

In [30]:
test.Date=test.Date.dt.strftime("%m-%d")

In [31]:
GCC_test=test[test["country"].isin(["Saudi Arabia","United Arab Emirates","Kuwait","Bahrain","Qatar","Oman"])]

In [32]:
GCC_test.Count=GCC_test.Count.astype("int")

C:\Users\ibrahim\Anaconda3\lib\site-packages\pandas\core\generic.py:5096: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy



In [33]:
import plotly.express as px

fig = px.bar(GCC_test[GCC_test["Date"]>"03-20"], x="country", y="Count", color="country",
  animation_frame="Date", animation_group="country", range_y=[0,40000])
fig.show()

In [34]:
import plotly.graph_objects as go

fig = go.Figure(data=go.Bar(x=GCC_country_df["country"],y=GCC_country_df["recovered"] , name='Recovered Cases'))
fig.add_trace(go.Bar(x=GCC_country_df["country"], y=GCC_country_df["active"], name='Active Cases'))


fig.update_layout(barmode='stack', xaxis={'categoryorder':'total descending'})
fig.update_layout( title="Active Cases VS Recovered Cases",
    xaxis_title="country",
    yaxis_title="No . Active and Recovered")
fig.show();


In [35]:
sorted_country_df = GCC_country_df.sort_values('percent', ascending= False)
fig=px.bar(sorted_country_df,x="country", y="percent" ,color_discrete_sequence=["#e40000"])
fig.update_layout( title="The most affected countries compared to their population % ",
    xaxis_title="country",
    yaxis_title="confirmed")
fig.show();

In [36]:
fig=px.bar(
    GCC_country_df,
    x = "country",
    y = "deaths",
    title= "Number of deaths", # the axis names
    color_discrete_sequence=["gray"], 
    height=500,
    width=800
)
fig.update_layout(barmode='stack', xaxis={'categoryorder':'total descending'})

In [37]:

opts=["Bahrain","Kuwait","Oman","Qatar","Saudi Arabia","United Arab Emirates"]
#opts=activeCase.country.values
widg=widgets.Dropdown(
    options=opts,
    value=opts[1],
    description="Country:")




    
widgets.interact(plot_cases_of_a_country,country=widg)




interactive(children=(Dropdown(description='Country:', index=1, options=('Bahrain', 'Kuwait', 'Oman', 'Qatar',…

<function __main__.plot_cases_of_a_country(country)>

In [38]:

test=country_df[['country','iso3']].merge(test)

In [39]:
country_df.tail(50)

country          last_update        lat       long_  \
132  Bosnia and Herzegovina  2020-08-03 14:34:52  43.915900   17.679100   
133       Equatorial Guinea  2020-08-03 14:34:52   1.650800   10.267900   
134                  Serbia  2020-08-03 14:34:52  44.016500   21.005900   
135                    Iran  2020-08-03 14:34:52  32.427908   53.688046   
136              Costa Rica  2020-08-03 14:34:52   9.748900  -83.753400   
137                   Italy  2020-08-03 14:34:52  41.871900   12.567400   
138   Sao Tome and Principe  2020-08-03 14:34:52   0.186360    6.613081   
139             Switzerland  2020-08-03 14:34:52  46.818200    8.227500   
140                Honduras  2020-08-03 14:34:52  15.200000  -86.241900   
141               Argentina  2020-08-03 14:34:52 -38.416100  -63.616700   
142          United Kingdom  2020-08-03 14:34:52  55.000000   -3.000000   
143              Cabo Verde  2020-08-03 14:34:52  16.538800  -23.041800   
144                Portugal  2020-08-03 14:34:52  39.399900   -8.224500   
145              Kazakhstan  2020-08-03 14:34:52  48.019600   66.923700   
146                 Ecuador  2020-08-03 14:34:52  -1.831200  -78.183400   
147              Montenegro  2020-08-03 14:34:52  42.708678   19.374390   
148         North Macedonia  2020-08-03 14:34:52  41.608600   21.745300   
149                 Iceland  2020-08-03 14:34:52  64.963100  -19.020800   
150                Djibouti  2020-08-03 14:34:52  11.825100   42.590300   
151                 Ireland  2020-08-03 14:34:52  53.142400   -7.692100   
152                  Russia  2020-08-03 14:34:52  61.524000  105.318800   
153              Kyrgyzstan  2020-08-03 14:34:52  41.204380   74.766098   
154                 Belgium  2020-08-03 14:34:52  50.833300    4.469936   
155                   Spain  2020-08-03 14:34:52  40.463667   -3.749220   
156    United Arab Emirates  2020-08-03 14:34:52  23.424076   53.847818   
157                Colombia  2020-08-03 14:34:52   4.570900  -74.297300   
158      Dominican Republic  2020-08-03 14:34:52  18.735700  -70.162700   
159                 Bolivia  2020-08-03 14:34:52 -16.290200  -63.588700   
160                 Belarus  2020-08-03 14:34:52  53.709800   27.953400   
161                  Sweden  2020-08-03 14:34:52  60.128200   18.643500   
162                Maldives  2020-08-03 14:34:52   3.202800   73.220700   
163                  Israel  2020-08-03 14:34:52  31.046051   34.851612   
164            Saudi Arabia  2020-08-03 14:34:52  23.885942   45.079162   
165            South Africa  2020-08-03 14:34:52 -30.559500   22.937500   
166               Singapore  2020-08-03 14:34:52   1.283300  103.833300   
167                 Moldova  2020-08-03 14:34:52  47.411600   28.369900   
168              Luxembourg  2020-08-03 14:34:52  49.815300    6.129600   
169                 Andorra  2020-08-03 14:34:52  42.506300    1.521800   
170                  Brazil  2020-08-03 14:34:52 -14.235000  -51.925300   
171                 Armenia  2020-08-03 14:34:52  40.069100   45.038200   
172                    Peru  2020-08-03 14:34:52  -9.190000  -75.015200   
173                      US  2020-08-03 14:34:52  40.000000 -100.000000   
174                  Panama  2020-08-03 14:34:52   8.538000  -80.782100   
175                    Oman  2020-08-03 14:34:52  21.512583   55.923255   
176                  Kuwait  2020-08-03 14:34:52  29.311660   47.481766   
177                   Chile  2020-08-03 14:34:52 -35.675100  -71.543000   
178              San Marino  2020-08-03 14:34:52  43.942400   12.457800   
179                 Bahrain  2020-08-03 14:34:52  26.027500   50.550000   
180                   Qatar  2020-08-03 14:34:52  25.354800   51.183900   
181                 Eritrea  2020-08-03 14:34:52  15.179400   39.782300   

     confirmed    deaths  recovered     active  incident_rate  people_tested  \
132    12462.0     362.0     6359.0     5741.0     379.844642            NaN   
133     4821.0      83.0     2182.

In [40]:
fig=px.bar(
    country_df.sort_values(by="deaths" , ascending=False).head(10),
    x = "country",
    y = "deaths",
    title= "Number of deaths", # the axis names
    color_discrete_sequence=["gray"], 
    height=500,
    width=800
)
fig.update_layout(barmode='stack', xaxis={'categoryorder':'total descending'})

In [41]:
import plotly.express as px

fig = px.choropleth(test, locations="iso3", color="Count", hover_name="country", animation_frame="Date",color_continuous_scale="YlOrRd")
fig.show()